In [1]:
import torch
import timm
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
from tqdm import tqdm

In [2]:
pretrained = timm.list_models(pretrained=True)
len(pretrained)

592

In [3]:
import json
with open('timm_model_input_sizes.json', 'r', encoding='utf-8') as f:
    sizes = json.load(f)

In [4]:
remaining = list(set(pretrained) - set(sizes['112']))
remaining.sort()

In [11]:
twotwentyfour = []
for name in tqdm(remaining):
    model = timm.create_model(name).to(device)
    try: 
        model(torch.randn(1,3,224,224).to(device))
        twotwentyfour += [name]
    except:
        continue


  1%|          | 1/174 [00:03<09:29,  3.29s/it]/nfshomes/sdooley1/anaconda3/lib/python3.9/site-packages/torch/functional.py:568: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ../aten/src/ATen/native/TensorShape.cpp:2228.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]
100%|██████████| 174/174 [04:26<00:00,  1.53s/it]


In [29]:
for model_name in list(set(pretrained) - set(sizes['224']) - set(sizes['112'])):
    backbone = timm.create_model(model_name, num_classes=0)
    config = timm.data.resolve_data_config({}, model=backbone)
    model_input_size = config['input_size'][1]
    if str(model_input_size) in sizes.keys():
        sizes[str(model_input_size)] += [model_name]
    else:
        sizes[str(model_input_size)] = [model_name]

In [32]:
import json
with open('timm_model_input_sizes.json', 'w', encoding='utf-8') as f:
    json.dump(sizes, f, ensure_ascii=False, indent=4)

# get batch_size information

In [84]:
# these models weren't run
non_compliant_models = list(set(timm.list_models('crossvit*',pretrained=True) + \
                                timm.list_models('*448*',pretrained=True) + \
                                timm.list_models('tresnet*',pretrained=True)))

In [85]:
import pandas as pd
import numpy as np
import glob
all_files = glob.glob("commands/seed222/remaining*")

li = []

for filename in all_files:
    df = pd.read_csv(filename, header=None, delim_whitespace=True)
    li.append(df)

frame = pd.concat(li, axis=0, ignore_index=True)
frame.columns = ['python3', 'file',
                 'backbone_arg', 'backbone_name', 
                 'input_size_arg','input_size',
                 'batch_size_arg', 'batch_size']

In [86]:
import pandas as pd
import glob
all_files = glob.glob("commands/seed222/112/*")

li = []

for filename in all_files:
    df = pd.read_csv(filename, header=None, delim_whitespace=True)
    li.append(df)

frame112 = pd.concat(li, axis=0, ignore_index=True)
frame112.columns = ['python3', 'file',
                 'backbone_arg', 'backbone_name', 
                 'batch_size_arg', 'batch_size']

In [115]:
all_backbones = pd.concat([frame,frame112], axis=0, ignore_index=True)
all_backbones = all_backbones.drop(all_backbones[all_backbones['backbone_name'].isin( non_compliant_models )].index)

duplicates = []
for m,df in iter(all_backbones.groupby('backbone_name')):
    if df.shape[0]>1:
        x_min = all_backbones[all_backbones['backbone_name']==m]['batch_size'].idxmin()
        indices = list(df.index)
        indices.remove(x_min)
        duplicates += indices
        
all_backbones = all_backbones.drop(duplicates)
all_backbones.input_size_arg = '--input_size'
all_backbones.input_size = all_backbones.input_size.replace(np.nan, 112)
all_backbones.input_size = all_backbones.input_size.astype(int)
all_backbones.batch_size = all_backbones.batch_size.astype(int)

all_backbones = all_backbones.sort_values(['input_size','batch_size'], ascending=[True,False])
all_backbones.to_csv('commands/commands.csv', index=False)

In [116]:
bb = pd.read_csv('commands/commands.csv')
bb = bb.sort_values(['input_size','batch_size'], ascending=[True,False])
bb['seed_arg'] = '--seed'
bb['seed'] = 223
bb.to_csv('commands/seed223.sh', sep=' ', index=False, header = False)

In [ ]:
bb.bat

In [2]:
results = pd.read_csv('results_nooversampling/timm_from-scratch.csv',sep='\t')

for s,foo in iter(results.groupby('epoch')):
    print(s, len(pd.unique(foo['Model'])))

finished_models = set(results[results['epoch'] == 2]['Model'])

-1 41
0 35
1 35
2 35


In [3]:
import pandas as pd

results = pd.read_csv('results_nooversampling/timm_from-scratch.csv',sep='\t')

for s,foo in iter(results.groupby('epoch')):
    print(s, len(pd.unique(foo['Model'])))

finished_models = set(results[results['epoch'] == 2]['Model'])

bb = pd.read_csv('commands/commands.csv')
bb = bb.sort_values(['input_size','batch_size'], ascending=[True,False])
bb['seed_arg'] = '--seed'
bb['seed'] = 222
bb['pretrained_arg'] = ''
bb['pretrained'] = ''
bb.file = '/cmlscratch/sdooley1/face.evoLVe.PyTorch/fairness_train_timm.py'
# bb = bb[bb.batch_size == 250]
bb = bb.loc[bb.apply(lambda x: x.backbone_name not in finished_models, axis=1)]
# bb.to_csv('commands/scratch.sh', sep=' ', index=False, header = False)

-1 187
0 178
1 176
2 176


In [5]:
bb[bb.batch_size == 100]

python3                                               file  \
187  python3  /cmlscratch/sdooley1/face.evoLVe.PyTorch/fairn...   
188  python3  /cmlscratch/sdooley1/face.evoLVe.PyTorch/fairn...   
189  python3  /cmlscratch/sdooley1/face.evoLVe.PyTorch/fairn...   
190  python3  /cmlscratch/sdooley1/face.evoLVe.PyTorch/fairn...   
191  python3  /cmlscratch/sdooley1/face.evoLVe.PyTorch/fairn...   
..       ...                                                ...   
444  python3  /cmlscratch/sdooley1/face.evoLVe.PyTorch/fairn...   
445  python3  /cmlscratch/sdooley1/face.evoLVe.PyTorch/fairn...   
446  python3  /cmlscratch/sdooley1/face.evoLVe.PyTorch/fairn...   
447  python3  /cmlscratch/sdooley1/face.evoLVe.PyTorch/fairn...   
448  python3  /cmlscratch/sdooley1/face.evoLVe.PyTorch/fairn...   

        backbone_arg                backbone_name input_size_arg  input_size  \
187  --backbone_name                    repvgg_b2   --input_size         112   
188  --backbone_name                  repvgg_b2g4   --input_size         112   
189  --backbone_name                  repvgg_b3g4   --input_size         112   
190  --backbone_name                        vgg11   --input_size         112   
191  --backbone_name                        vgg13   --input_size         112   
..               ...                          ...            ...         ...   
444  --backbone_name  vit_small_patch32_224_in21k   --input_size         224   
445  --backbone_name        vit_small_r26_s32_224   --input_size         224   
446  --backbone_name         vit_tiny_patch16_224   --input_size         224   
447  --backbone_name   vit_tiny_patch16_224_in21k   --input_size         224   
448  --backbone_name  vit_tiny_r_s16_p8_224_in21k   --input_size         224   

    batch_size_arg  batch_size seed_arg  seed pretrained_arg pretrained  
187   --batch_size         100   --seed   222                            
188   --batch_size         100   --seed   222                            
189   --batch_size         100   --seed   222                            
190   --batch_size         100   --seed   222                            
191   --batch_size         100   --seed   222                            
..             ...         ...      ...   ...            ...        ...  
444   --batch_size         100   --seed   222                            
445   --batch_size         100   --seed   222                            
446   --batch_size         100   --seed   222                            
447   --batch_size         100   --seed   222                            
448   --batch_size         100   --seed   222                            

[152 rows x 12 columns]

In [7]:
import pandas as pd
df = pd.read_csv('pretrained.sh', header=None, delim_whitespace=True)

df.columns = ['python3', 'file',
                 'backbone_arg', 'backbone_name', 
                 'input_size_arg','input_size',
                 'batch_size_arg', 'batch_size',
             'seed_arg','seed',
             'pretrained_arg','pretrained']
df.to_csv('commands/commands.csv',index=False)

# fix failed jobs

In [8]:
with open('seed226.sh') as f:
    all226 = f.readlines()

with open('seed227.sh') as f:
    all227 = f.readlines()

with open('failed_226.txt') as f:
    failed226 = f.readlines()

with open('failed_227.txt') as f:
    failed227 = f.readlines()


In [6]:
failed226_indices = [int(x.split(' ')[0].split('_')[1]) for x in failed226]
failed227_indices = [int(x.split(' ')[0].split('_')[1]) for x in failed227]

In [11]:
redo_these = [all226[i] for i in failed226_indices] + [all227[i] for i in failed227_indices]
with open('redo_these_1.sh', mode="w") as f:  # also, tried mode="rb"
    for s in redo_these:
        f.write("%s\n" % s)


In [133]:
import pandas as pd
results = pd.read_csv('results_nooversampling/timm_bias_celeba_balanced_ratio_cos.csv',sep='\t')


In [134]:
for s,foo in iter(results.groupby('seed')):
    print(s, len(pd.unique(foo['Model'])))

222.0 573
223.0 573
224.0 573
225.0 573
226.0 537
227.0 307


In [135]:
with open('seed226.sh') as f:
    all226 = f.readlines()
    
missed_226 = [x for x in all226 if x.split(' ')[3] in (set(results[results.seed == 224]['Model']) - set(results[results.seed == 226]['Model']))]

In [136]:
with open('seed227.sh') as f:
    all227 = f.readlines()
    
missed_227 = [x for x in all227 if x.split(' ')[3] in (set(results[results.seed == 224]['Model']) - set(results[results.seed == 227]['Model']))]

In [137]:
redo_these = missed_226 + missed_227
with open('redo_these_1.sh', mode="w") as f:  # also, tried mode="rb"
    for s in redo_these:
        f.write("%s" % s)


In [138]:
len(redo_these)

302

# combine results with metadata

In [15]:
import pandas as pd
import numpy as np
meta = pd.read_csv('timm_model_metadata.csv')
results = pd.read_csv('results_nooversampling/timm_pretrained.csv',sep='\t')

results = results.drop_duplicates(
  subset = ['Model', 'seed'],
  keep = 'last').reset_index(drop = True)

results = results.merge(meta, left_on='Model', right_on='model_name')

In [16]:
results

Model                                  uuid  \
0          adv_inception_v3  131bfaaf-5563-437e-88a5-1132bdfd6d70   
1          adv_inception_v3  131bfaaf-5563-437e-88a5-1132bdfd6d70   
2          adv_inception_v3  131bfaaf-5563-437e-88a5-1132bdfd6d70   
3          adv_inception_v3  131bfaaf-5563-437e-88a5-1132bdfd6d70   
4          adv_inception_v3  131bfaaf-5563-437e-88a5-1132bdfd6d70   
...                     ...                                   ...   
5725  vit_large_patch16_384  8130ef4e-db1a-4541-aeca-91862c49bfbb   
5726  vit_large_patch16_384  8a0b4713-5d30-47f9-9130-404d80aecb29   
5727  vit_large_patch16_384  a0bc3e7b-549b-43fb-8d92-a7f1be09564c   
5728  vit_large_patch16_384  2edf1652-0c74-4827-a58e-86e32f8754c9   
5729  vit_large_patch16_384  a262315b-1e0f-4944-80e6-e8489bce02b4   

      Idx training ratio male  Idx training ratio female  \
0                         1.0                        1.0   
1                         1.0                        1.0   
2                         1.0                        1.0   
3                         1.0                        1.0   
4                         1.0                        1.0   
...                       ...                        ...   
5725                      1.0                        1.0   
5726                      1.0                        1.0   
5727                      1.0                        1.0   
5728                      1.0                        1.0   
5729                      1.0                        1.0   

      Img training ratio male  Img training ratio female  \
0                         1.0                        1.0   
1                         1.0                        1.0   
2                         1.0                        1.0   
3                         1.0                        1.0   
4                         1.0                        1.0   
...                       ...                        ...   
5725                      1.0                        1.0   
5726                      1.0                        1.0   
5727                      1.0                        1.0   
5728                      1.0                        1.0   
5729                      1.0                        1.0   

                                                   Data  P identities male  \
0     /cmlscratch/sdooley1/data/CelebA/Img/img_align...                1.0   
1     /cmlscratch/sdooley1/data/CelebA/Img/img_align...                1.0   
2     /cmlscratch/sdooley1/data/CelebA/Img/img_align...                1.0   
3     /cmlscratch/sdooley1/data/CelebA/Img/img_align...                1.0   
4     /cmlscratch/sdooley1/data/CelebA/Img/img_align...                1.0   
...                                                 ...                ...   
5725  /cmlscratch/sdooley1/data/CelebA/Img/img_align...                1.0   
5726  /cmlscratch/sdooley1/data/CelebA/Img/img_align...                1.0   
5727  /cmlscratch/sdooley1/data/CelebA/Img/img_align...                1.0   
5728  /cmlscratch/sdooley1/data/CelebA/Img/img_align...                1.0   
5729  /cmlscratch/sdooley1/data/CelebA/Img/img_align...                1.0   

      P identities female  P images male  ...  RadixSoftmax  GroupNorm  \
0                     1.0            1.0  ...           NaN        NaN   
1                     1.0            1.0  ...           NaN        NaN   
2                     1.0            1.0  ...           NaN        NaN   
3                     1.0            1.0  ...           NaN        NaN   
4                     1.0            1.0  ...           NaN        NaN   
...                   ...            ...  ...           ...        ...   
5725                  1.0            1.0  ...           NaN        NaN   
5726                  1.0            1.0  ...           NaN        NaN   
5727                  1.0            1.0  ...           NaN        NaN   
5728                  1.0            1.0  ...           NaN        NaN   


In [5]:
import numpy as np
import plotly
from plotly import graph_objects as go
from plotly.colors import DEFAULT_PLOTLY_COLORS
from sklearn.datasets import load_iris
from sklearn.decomposition import PCA


def confidence_ellipse(x, y, n_std=1.96, size=100):
    """
    Get the covariance confidence ellipse of *x* and *y*.
    Parameters
    ----------
    x, y : array-like, shape (n, )
        Input data.
    n_std : float
        The number of standard deviations to determine the ellipse's radiuses.
    size : int
        Number of points defining the ellipse
    Returns
    -------
    String containing an SVG path for the ellipse
    
    References (H/T)
    ----------------
    https://matplotlib.org/3.1.1/gallery/statistics/confidence_ellipse.html
    https://community.plotly.com/t/arc-shape-with-path/7205/5
    """
    if x.size != y.size:
        raise ValueError("x and y must be the same size")

    cov = np.cov(x, y)
    pearson = cov[0, 1]/np.sqrt(cov[0, 0] * cov[1, 1])
    # Using a special case to obtain the eigenvalues of this
    # two-dimensionl dataset.
    ell_radius_x = np.sqrt(1 + pearson)
    ell_radius_y = np.sqrt(1 - pearson)
    theta = np.linspace(0, 2 * np.pi, size)
    ellipse_coords = np.column_stack([ell_radius_x * np.cos(theta), ell_radius_y * np.sin(theta)])
    
    # Calculating the stdandard deviation of x from
    # the squareroot of the variance and multiplying
    # with the given number of standard deviations.
    x_scale = np.sqrt(cov[0, 0]) * n_std
    x_mean = np.mean(x)

    # calculating the stdandard deviation of y ...
    y_scale = np.sqrt(cov[1, 1]) * n_std
    y_mean = np.mean(y)
  
    translation_matrix = np.tile([x_mean, y_mean], (ellipse_coords.shape[0], 1))
    rotation_matrix = np.array([[np.cos(np.pi / 4), np.sin(np.pi / 4)],
                                [-np.sin(np.pi / 4), np.cos(np.pi / 4)]])
    scale_matrix = np.array([[x_scale, 0],
                            [0, y_scale]])
    ellipse_coords = ellipse_coords.dot(rotation_matrix).dot(scale_matrix) + translation_matrix
        
    path = f'M {ellipse_coords[0, 0]}, {ellipse_coords[0, 1]}'
    for k in range(1, len(ellipse_coords)):
        path += f'L{ellipse_coords[k, 0]}, {ellipse_coords[k, 1]}'
    path += ' Z'
    return path

In [ ]:
fig = go.Figure()

model_types = list(np.unique(results.model_type))
model_types.sort()

traces = []


for a,b in iter(results.groupby('model_type')):
    x,y,m_names = [], [], []
    m_type = list(b.model_type)[0]
    
    color = plotly.colors.qualitative.Light24[model_types.index(m_type) % 24]
    for a2,b2 in iter(b.groupby('model_name')):
        m_names += [a2]
        x += [b2['Acc m'].mean()]
        y += [b2['Acc f'].mean()]
        fig.add_shape(type='path',
                      path=confidence_ellipse(b2['Acc m'], b2['Acc f']),
                      line={'dash': 'dot'},
                      line_color=color)
    fig.add_trace(
        go.Scatter(
            x=x,
            y=y,
            name=m_type,
            text = m_names,
            mode='markers',
            marker={'color': color}
        )
    )    
    
    
    
fig.add_shape(type='line',
              x0=0,
              y0=0,
              x1=23,
              y1=23,
              line=dict(color='Black'))

# fig.write_html("sample_figure.html")
fig.show()

In [28]:
fig = go.Figure()

model_types = list(np.unique(results.model_type))
model_types.sort()

traces = []


for a,b in iter(results.groupby('model_type')):
    x,y,m_names = [], [], []
    m_type = list(b.model_type)[0]
    
    color = plotly.colors.qualitative.Light24[model_types.index(m_type) % 24]
    for a2,b2 in iter(b.groupby('model_name')):
        m_names += [' '.join([m_type,a2])]
        x += [b2['Acc m'].mean()]
        y += [b2['Acc f'].mean()]
        fig.add_shape(type='path',
                      path=confidence_ellipse(b2['Acc m'], b2['Acc f']),
                      line={'dash': 'dot'},
                      line_color=color,
                      name = 'error_bars'
                     )
    fig.add_trace(
        go.Scatter(
            x=x,
            y=y,
            name=m_type,
            text = m_names,
            mode='markers',
            marker={'color': color}
        )
    )    
    
    
    
fig.add_shape(type='line',
              x0=0,
              y0=0,
              x1=52,
              y1=52,
              line=dict(color='Black'))

fig.update_layout(
    title="Disparities in Facial Recognition (identification)\nPretrained",
    xaxis_title="Accuracy on Males",
    yaxis_title="Accuracy on Females",
    legend_title="Type of Model",
)


# fig.write_html("pre-trained_with_error.html")
fig.show()